![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 6,7. <i>Preprocessing i postprocessing</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Na dzisiejszych zajęciach zajmiemy się niezwykle przydatnymi narzędziami wspomagającymi pracę tłumacza. W odróżnieniu od dotychczas poznanych, nie są one oparte na pamięci tłumaczeń, ani na słownikach. Chodzi o techniki preprocessingu i postprocessingu.

Proces tłumaczenia przeprowadzony w pełni profesjonalnie składa się z wielu faz, które angażują nie tylko tłumaczy, ale także kierowników projektu, analityków, czy korektorów. Każda z tych osób do swojej pracy może wykorzystywać system informatyczny, do którego na początku całego procesu trafiają pliki do tłumaczenia. Oznacza to, że zanim tekst źródłowy trafi do tłumacza, system ma jeszcze szansę coś w nim zmienić. A kiedy tłumacz wykona już swoją pracę, można uruchomić kolejny mechanizm, który zmodyfikuje tłumaczenie przed oddaniem go do zamawiającego. Jak się domyślamy, modyfikacje tekstu przed przekazaniem go do tłumacza nazywamy **preprocessingiem**, natomiast te dokonywane po wykonaniu tłumaczenia (ale przed zwróceniem go do klienta) nazywamy **postprocessingiem**. Terminy te, będące mało zgrabnymi kalkami z języka angielskiego, mają wersje prawdziwie polskie: przetwarzanie wstępne i końcowe. Wersje te są jednak stosowane na tyle rzadko, że mogą jedynie wprowadzić zamieszanie (co w gruncie rzeczy jest dość smutne).

Typowe operacje w fazie preprocessingu obejmują:
* identyfikację tagów xmlowych (które często są później wyświetlane w interfejsie CAT-a jako jeden niepodzielny znak)
* identyfikację segmentów, których nie należy tłumaczyć (na przykład składających się z samych liczb)

* identyfikację dat i jednostek miary w tekście źródłowym

We wszystkich tych operacjach niezwykle przydatne okazują się wyrażenia regularne.

### Ćwiczenie 1: Używając wyrażeń regularnych napisz funkcję do znajdowania wszystkich tagów XML w tekście. Funkcja powinna zwracać pozycje, na których znalazła tagi.

In [91]:
import re    

text = "<root><name>John</name><age>30</age></root>"

def find_tags(text):
    xml_tag_pattern = r"<[^>]+>"

    tags_positions = [{match.group(): (match.start(), match.end())} for match in re.finditer(xml_tag_pattern, text)]
    
    return tags_positions

find_tags(text)


[{'<root>': (0, 6)},
 {'<name>': (6, 12)},
 {'</name>': (16, 23)},
 {'<age>': (23, 28)},
 {'</age>': (30, 36)},
 {'</root>': (36, 43)}]

### Ćwiczenie 2: Używając wyrażeń regularnych napisz funkcję do identyfikacji segmentów, których nie należy tłumaczyć. Zastosuj wymyślone przez siebie kryteria. Funkcja is_translatable powinna zwracać True, jeśli segment powinien być przetłumaczony przez tłumacza (zwykłe zdanie). False powinno być zwrócone, kiedy segment jest nieprzetłumaczalny i powinien zostać skopiowany (np. 4.2.1.)

In [92]:

import re

def is_translatable(text):
    non_translatable_pattern = r'<[^>]+>'

    if re.match(non_translatable_pattern, text.strip()):
        return False 
    return True

texts = [
    "test",
    "<4.2.1>",
    "<text>",
    "<1.2.4>",
    "test",
    "test324234",
    "test32443242",
    "1.2.4",
    "4.2.1",
    ">",
    "<",
    "><",
]

for text in texts:
    print(f"{text}: {is_translatable(text)}")



test: True
<4.2.1>: False
<text>: False
<1.2.4>: False
test: True
test324234: True
test32443242: True
1.2.4: True
4.2.1: True
>: True
<: True
><: True


### Ćwiczenie 3: Używając wyrażeń regularnych napisz funkcję do identyfikacji i interpretacji 5 wybranych przez siebie formatów daty. Funkcja powinna zwracać pozycje, na których odnalazła daty oraz dzień, miesiąc i rok, które ta data reprezentuje.

In [93]:
def find_dates(text):
    patterns = [
        r'(\d{2})/(\d{2})/(\d{4})',    # DD/MM/RRRR
        r'(\d{2})-(\d{2})-(\d{4})',    # DD-MM-RRRR
        r'(\d{2}).(\d{2}).(\d{4})',    # DD.MM.RRRR
        r'(\d{2}) (\d{2}) (\d{4})',    # DD MM RRRR
        r'(\d{2})/(\d{2})/(\d{2})'     # DD/MM/RR
    ]

    date_formats = [
        "DD/MM/RRRR",
        "DD-MM-RRRR",
        "DD.MM.RRRR",
        "DD MM RRRR",
        "DD/MM/RR"
    ]

    results = []
    for pattern, date_format in zip(patterns, date_formats):
        for match in re.finditer(pattern, text):
                day, month, year = match.groups()
                results.append({
                    "position": match.span(),
                    "date_format": date_format,
                    "day": int(day),
                    "month": int(month),
                    "year": int(year)
                })

    return results

text = "Data dsadasdj12/04/2024 oraz dnasjdjasndj02-12-2023, jeszcze 12/04/2024 i 04.12.24 oraz 20/04/24."

find_dates(text)


[{'position': (13, 23),
  'date_format': 'DD/MM/RRRR',
  'day': 12,
  'month': 4,
  'year': 2024},
 {'position': (61, 71),
  'date_format': 'DD/MM/RRRR',
  'day': 12,
  'month': 4,
  'year': 2024},
 {'position': (41, 51),
  'date_format': 'DD-MM-RRRR',
  'day': 2,
  'month': 12,
  'year': 2023},
 {'position': (13, 23),
  'date_format': 'DD.MM.RRRR',
  'day': 12,
  'month': 4,
  'year': 2024},
 {'position': (41, 51),
  'date_format': 'DD.MM.RRRR',
  'day': 2,
  'month': 12,
  'year': 2023},
 {'position': (61, 71),
  'date_format': 'DD.MM.RRRR',
  'day': 12,
  'month': 4,
  'year': 2024},
 {'position': (13, 21),
  'date_format': 'DD/MM/RR',
  'day': 12,
  'month': 4,
  'year': 20},
 {'position': (61, 69),
  'date_format': 'DD/MM/RR',
  'day': 12,
  'month': 4,
  'year': 20},
 {'position': (88, 96),
  'date_format': 'DD/MM/RR',
  'day': 20,
  'month': 4,
  'year': 24}]

Po preprocessingu i tłumaczeniu czas na postprocessing. Ponieważ wykonywany jest on na przetłumaczonym tekście, jego głównym zadaniem jest eliminacja błędów popełnionych przez tłumacza w fazie tłumaczenia. Podczas postprocessingu najczęściej wykonuje się:
* korektę pisowni dla języka docelowego
* usuwanie błędów typograficznych z tekstu (np. wielokrotne spacje, brak spacji po przecinku)
Stanowi to bardzo ważne wsparcie dla edytorów i korektorów, czyli osób sprawdzających pracę tłumacza.

Jednak nowoczesne CAT-y potrafią coś jeszcze. Są w stanie w sprytny sposób wykorzystać kombinację pre- i postprocessingu do wyręczenia tłumacza w żmudnych i technicznych czynnościach. Wykonajmy następujące ćwiczenie:

### Ćwiczenie 4: Wykorzystując funkcję find_dates napisz funkcję do obsługi dat w tłumaczeniu. Wejściem jest segment źródłowy oraz docelowy, które zawierają daty, przy czym daty te mogą być w różnych formatach. Dodatkowym parametrem wejściowym jest nazwa oczekiwanego formatu daty w tłumaczeniu (np. "Europe", "US", "digit-dot". Funkcja najpierw sprawdza, czy liczba dat w tłumaczeniu zgadza się z liczbą dat w segmencie źródłowym oraz czy odpowiadające sobie daty wskazują na ten sam dzień. Jeśli nie, wypisywane jest stosowne ostrzeżenie. Oczekiwanym wyjściem jest segment docelowy, w którym wszystkie daty są w żądanym formacie. 

In [94]:
from queue import Full
import re

date_formats = [
        r'\1/\2/\3',
        r'\1-\2-\3',
        r'\1.\2.\3',
        r'\1 \2 \3',
        r'\1/\2/\3',
    ]

patterns = [
        r'(\d{2})/(\d{2})/(\d{4})',    # DD/MM/RRRR
        r'(\d{2})-(\d{2})-(\d{4})',    # DD-MM-RRRR
        r'(\d{2}).(\d{2}).(\d{4})',    # DD.MM.RRRR
        r'(\d{2}) (\d{2}) (\d{4})',    # DD MM RRRR
        r'(\d{2})/(\d{2})/(\d{2})'     # DD/MM/RR
    ]


def find_dates(text):
   
    results = []
    for pattern, date_format in zip(patterns, date_formats):
        for match in re.finditer(pattern, text):
            day, month, year = match.groups()
            results.append({
                "position": match.span(),
                "date_format": date_format,
                "day": int(day),
                "month": int(month),
                "year": int(year)
            })

    return results


def translate_dates(source_text, target_text, target_format):
    source_dates = find_dates(source_text)
    target_dates = find_dates(target_text)
    print(target_dates)
    print('\n')

    if len(source_dates) != len(target_dates):
        print("Uwaga: Rózna liczba dat")
        return

    for source_date, target_date in zip(source_dates, target_dates):
        if f"{source_date['day']}/{source_date['month']}/{source_date['year']}" != f"{target_date['day']}/{target_date['month']}/{target_date['year']}":
            print("Uwaga: Daty są rózne")
            return
        
    replacement = ''
    if target_format == "Europe":
        replacement = r'\1/\2/\3'
    elif target_format == "US":
        replacement = r'\1/\2/\3'
    elif target_format == "digit-dot":
        replacement = r'\1.\2.\3'
    else:
        print("Uwaga: Niewspierany format.")
        return

      

    final_text = target_text

    for pattern in patterns:
      final_text = re.sub(pattern, replacement, final_text)

    return final_text

# Example usage:
source_text = "Today is 21 04 2021 and tomorrow will be 21/04/2024."
target_text = "Aujourd'hui, c'est le 21 04 2021 et demain ce sera le 21/04/2024."
translated_text = translate_dates(source_text, target_text, "digit-dot")
print("Translated text (Europe format):", translated_text)





[{'position': (54, 64), 'date_format': '\\1/\\2/\\3', 'day': 21, 'month': 4, 'year': 2024}, {'position': (22, 32), 'date_format': '\\1.\\2.\\3', 'day': 21, 'month': 4, 'year': 2021}, {'position': (54, 64), 'date_format': '\\1.\\2.\\3', 'day': 21, 'month': 4, 'year': 2024}, {'position': (22, 32), 'date_format': '\\1 \\2 \\3', 'day': 21, 'month': 4, 'year': 2021}, {'position': (54, 62), 'date_format': '\\1/\\2/\\3', 'day': 21, 'month': 4, 'year': 20}]


Translated text (Europe format): Aujourd'hui, c'est le 21.04.2021 et demain ce sera le 21.04.2024.


Co jeszcze można zrobić? Zajmijmy się tagami XML. Z punktu widzenia tłumacza najlepiej byłoby, gdyby mógł przetłumaczyć segment źródłowy zawierający tagi XML na język docelowy zupełnie ignorując te tagi. Ponieważ jednak tagi muszą jakoś znaleźć się w segmencie docelowym, przydałaby się jakaś "magiczna różdżka", która przeniosłaby wszystkie tagi ze źródła do tłumaczenia na mniej więcej dobre miejsca. Spełnijmy marzenie tłumacza!

Rozważmy następujący algorytm: na wejściu mamy segment źródłowy zawierający tagi oraz segment docelowy bez tagów. Dokonujemy tokenizacji segmentu źródłowego tak, aby tagi były osobnymi tokenami. Następnie przeprowadźmy tokenizację segmentu docelowego. Gdy to jest gotowe, możemy zabrać się za przenoszenie (kopiowanie) tagów z segmentu źródłowego do docelowego.

![Transfer tagów](img/tagtransfer.png)

Gdzie w segmencie docelowym powinien trafić tag? Przede wszystkim pomiędzy tokeny - nie chcemy rozbijać słów tagami. Pytanie tylko, pomiędzy które tokeny? Jeśli sytuacja jest taka, jak powyżej, kiedy segment źródłowy i docelowy mają taką samą liczbę słów nie będących tagami, przenosimy tagi na odpowiadające pozycje w tłumaczeniu. Natomiast jeśli długość tłumaczenia jest inna niż źródła, należy obliczać te pozycje w sposób proporcjonalny - jeśli np. mamy tag w źródle na pozycji 3, a tłumaczenie jest dwa razy dłuższe niż źródło, tag powinien być przeniesiony do tłumaczenia na pozycję 6. W przypadku niecałkowitych wartości proporcji stosujemy zaokrąglenia.

### Ćwiczenie 5: Zaimplementuj opisany algorytm transferu tagów.

In [153]:
import re

def split_text(text):
    parts = re.split(r'(<\w+>|<\/\w+>| )', text)
    
    split_list = []
    
    for part in parts:
        if part.strip():  
            split_list.append((part, part.startswith("<") and part.endswith(">")))
    
    return split_list

def transfer_tags(source_segment, target_segment):
    source_interation_index = 0

    split_source_segment = split_text(source_segment)

    target_text_with_tags = ''

    for text in target_segment.split():
        source_element  = split_source_segment[source_interation_index]
        
        while(source_element[1]):
            target_text_with_tags += source_element[0]
            source_interation_index = source_interation_index + 1
            source_element  = split_source_segment[source_interation_index]

        target_text_with_tags +=  text + ' '
        source_interation_index = source_interation_index + 1

    for index in range(source_interation_index, len(split_source_segment)):
        target_text_with_tags += split_source_segment[index][0]

    return target_text_with_tags


source_segment = "<greeting>Hello</greeting> <name>Ania!</name></name></name></name></name>John</name>"
target_segment = "Witaj Ania! John"

transfer_tags(source_segment,target_segment)


'<greeting>Witaj </greeting><name>Ania! </name></name></name></name></name>John </name>'